## Business Problem:

    The company is going to open a retirement home in Toronto, Canada, for those people who voluntarily seek for some company and help. The retirement house will give their customers housekeeping, periodic medical checks, and entertainment so they can enjoy their retirement.
    
    To achieve this, the company decided to open the retirement home in L’Amoreaux (117) based on the following criteria: over 1400 85+ People, >5000 65+ Senior people, and access to some amenities nearby such as banks, pools, gym, and restaurants. 
    
     The dataset was downloaded from https://www.toronto.ca/city-government/data-research-maps/open-data/, where I found the neighborhood boundaries and the data related to demographic characteristics of those.
 
    To Analyze our problem. First, I made a Choropleth map locating that Neighborhood that is overpopulated in other to avoid those for further selection. Then I filtered the data into a new data set that included only those neighborhoods that have over 5000 with 65+ years old and over 1000 85+ years old. Then I obtained the venues for those places from four square and checked which of the Neighborhood that met all the criteria.


In [3]:
!conda install geopandas

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopandas


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    proj4-5.2.0                |       he6710b0_1         7.0 MB
    munch-2.5.0                |             py_0          16 KB
    click-plugins-1.1.1        |             py_0          11 KB
    json-c-0.13.1              |       h1bed415_0          70 KB
    freexl-1.0.5               |       h14c3975_0          44 KB
    openjpeg-2.3.0             |       h05c96fa_1         456 KB
    pyproj-1.9.6               |   py36h14380d9_0          76 KB
    libkml-1.3.0               |       h590aaf7_4         633 KB
    gdal-2.3.3                 |   py36hbb2a789_0         1.3 MB
    poppler-0.65.0             |       h581218d_1         1.6 MB
    libspatialite-4.3.0a       |      hb08deb6_19         3.1 MB


In [106]:
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
from shapely.geometry import Point, Polygon
%matplotlib inline
import pickle
import numpy as np 
import requests

In [17]:
# The code was removed by Watson Studio for sharing.

Neighbourhood Number  Population, 2016  Population, 2011  \
0                   129             29113             30279   
1                   128             23757             21988   
2                    20             12054             11904   
3                    95             30526             29177   
4                    42             27695             26918   

   Population Change 2011-2016  Total private dwellings  \
0                       -0.039                     9371   
1                        0.080                     8535   
2                        0.013                     4732   
3                        0.046                    18109   
4                        0.029                    12473   

   Private dwellings occupied by usual residents  \
0                                           9120   
1                                           8136   
2                                           4616   
3                                          15934   
4                                          12124   

   Population density per square kilometre  Land area in square kilometres  \
0                                     3929                            7.41   
1                                     3034                            7.83   
2                                     2435                            4.95   
3                                    10863                            2.81   
4                                     2775                            9.98   

   Children (0-14 years)  Youth (15-24 years)  ...  External migrants  \
0                   3840                 3705  ...                605   
1                   3075                 3360  ...                490   
2                   1760                 1235  ...                 70   
3                   2360                 3750  ...                835   
4                   3605                 2730  ...                380   

   Total - Mobility status 5 years ago - 25% sample data  Non-movers 1  \
0                                              27490             18865   
1                                              22325             13565   
2                                              11370              8235   
3                                              27715             12980   
4                                              25925             16300   

   Movers 1  Non-migrants 1  Migrants 1  Internal migrants 1  \
0      8610            5445        3170                  880   
1      8775            5610        3145                  980   
2      3130            2200         925                  680   
3     14735            8340        6390                 3930   
4      9625            6480        3140                 1405   

   Intraprovincial migrants 1  Interprovincial migrants 1  External migrants 1  
0                         735                         135                 2280  
1                         760                         220                 2170  
2                         615                          70                  245  
3                        2630                        1310                 2460  
4                        1190                         220                 1735  

[5 rows x 2382 columns]

In [35]:

# Your data file was loaded into a botocore.response.StreamingBody object.
# Please read the documentation of ibm_boto3 and pandas to learn more about the possibilities to load the data.
# ibm_boto3 documentation: https://ibm.github.io/ibm-cos-sdk-python/
# pandas documentation: http://pandas.pydata.org/
streaming_body_1 = client_931862fd34264921bb0e905eeb14a6da.get_object(Bucket='ibmdatasciencecapstone-donotdelete-pr-x72bgdzud2ihzc', Key='Neighbourhoods.geojson')['Body']
# add missing __iter__ method so pandas accepts body as file-like object
if not hasattr(streaming_body_1, "__iter__"): streaming_body_1.__iter__ = types.MethodType( __iter__, streaming_body_1 ) 


In [20]:
readrawdata = streaming_body_1.read()

In [46]:
import fiona

In [48]:
with fiona.BytesCollection(readrawdata) as f:
    crs = f.crs
    map = gpd.GeoDataFrame.from_features(f, crs=crs)
    print(map.head())

   AREA_ATTR_ID                     AREA_DESC   AREA_ID  AREA_LONG_CODE  \
0      25926662                 Wychwood (94)  25886861              94   
1      25926663          Yonge-Eglinton (100)  25886820             100   
2      25926664           Yonge-St.Clair (97)  25886834              97   
3      25926665  York University Heights (27)  25886593              27   
4      25926666       Yorkdale-Glen Park (31)  25886688              31   

                      AREA_NAME  AREA_SHORT_CODE   LATITUDE  LONGITUDE  \
0                 Wychwood (94)               94  43.676919 -79.425515   
1          Yonge-Eglinton (100)              100  43.704689 -79.403590   
2           Yonge-St.Clair (97)               97  43.687859 -79.397871   
3  York University Heights (27)               27  43.765736 -79.488883   
4       Yorkdale-Glen Park (31)               31  43.714672 -79.457108   

   OBJECTID  PARENT_AREA_ID   Shape__Area  Shape__Length     X     Y   _id  \
0  16491505           4988

In [49]:
map.head()

AREA_ATTR_ID                     AREA_DESC   AREA_ID  AREA_LONG_CODE  \
0      25926662                 Wychwood (94)  25886861              94   
1      25926663          Yonge-Eglinton (100)  25886820             100   
2      25926664           Yonge-St.Clair (97)  25886834              97   
3      25926665  York University Heights (27)  25886593              27   
4      25926666       Yorkdale-Glen Park (31)  25886688              31   

                      AREA_NAME  AREA_SHORT_CODE   LATITUDE  LONGITUDE  \
0                 Wychwood (94)               94  43.676919 -79.425515   
1          Yonge-Eglinton (100)              100  43.704689 -79.403590   
2           Yonge-St.Clair (97)               97  43.687859 -79.397871   
3  York University Heights (27)               27  43.765736 -79.488883   
4       Yorkdale-Glen Park (31)               31  43.714672 -79.457108   

   OBJECTID  PARENT_AREA_ID   Shape__Area  Shape__Length     X     Y   _id  \
0  16491505           49885  3.217960e+06    7515.779658  None  None  3921   
1  16491521           49885  3.160334e+06    7872.021074  None  None  3922   
2  16491537           49885  2.222464e+06    8130.411276  None  None  3923   
3  16491553           49885  2.541821e+07   25632.335242  None  None  3924   
4  16491569           49885  1.156669e+07   13953.408098  None  None  3925   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

In [25]:
!conda install  pypi-packagename

Solving environment: failed

PackagesNotFoundError: The following packages are not available from current channels:

  - pypi-packagename

Current channels:

  - https://repo.anaconda.com/pkgs/main/linux-64
  - https://repo.anaconda.com/pkgs/main/noarch

To search for alternate channels that may provide the conda package you're
looking for, navigate to

    https://anaconda.org

and use the search bar at the top of the page.




In [53]:
!pip install folium

     |████████████████████████████████| 92kB 14.6MB/s eta 0:00:01


In [54]:
latitude = 43.653963
longitude = -79.387207

In [55]:
import folium

In [56]:
toronto_map = folium.Map(
                location = [latitude, longitude], 
                zoom_start = 10)

In [57]:

folium.Choropleth(
    geo_data=map,
    name='choropleth',
    data=data,
    columns=['Neighbourhood Number', 'Population, 2016'],
    key_on='feature.properties.AREA_SHORT_CODE',
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2,
).add_to(toronto_map)

folium.LayerControl().add_to(toronto_map)

In [58]:
toronto_map

In [59]:
map.head()

AREA_ATTR_ID                     AREA_DESC   AREA_ID  AREA_LONG_CODE  \
0      25926662                 Wychwood (94)  25886861              94   
1      25926663          Yonge-Eglinton (100)  25886820             100   
2      25926664           Yonge-St.Clair (97)  25886834              97   
3      25926665  York University Heights (27)  25886593              27   
4      25926666       Yorkdale-Glen Park (31)  25886688              31   

                      AREA_NAME  AREA_SHORT_CODE   LATITUDE  LONGITUDE  \
0                 Wychwood (94)               94  43.676919 -79.425515   
1          Yonge-Eglinton (100)              100  43.704689 -79.403590   
2           Yonge-St.Clair (97)               97  43.687859 -79.397871   
3  York University Heights (27)               27  43.765736 -79.488883   
4       Yorkdale-Glen Park (31)               31  43.714672 -79.457108   

   OBJECTID  PARENT_AREA_ID   Shape__Area  Shape__Length     X     Y   _id  \
0  16491505           49885  3.217960e+06    7515.779658  None  None  3921   
1  16491521           49885  3.160334e+06    7872.021074  None  None  3922   
2  16491537           49885  2.222464e+06    8130.411276  None  None  3923   
3  16491553           49885  2.541821e+07   25632.335242  None  None  3924   
4  16491569           49885  1.156669e+07   13953.408098  None  None  3925   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

In [60]:
data = data.loc[:, 'Neighbourhood Number':'Older Seniors (85+ years)']

In [61]:
data2 = data[data['Seniors (65+ years)'] > 5000]

In [62]:
data65 = data2[data2['Older Seniors (85+ years)']> 1000]

In [63]:
toronto_map65 = folium.Map(
                location = [latitude, longitude], 
                zoom_start = 10)

In [64]:
data65.head()

Neighbourhood Number  Population, 2016  Population, 2011  \
3                      95             30526             29177   
4                      42             27695             26918   
58                     14             43965             38084   
66                    117             43993             44919   
114                   118             27446             27398   

     Population Change 2011-2016  Total private dwellings  \
3                          0.046                    18109   
4                          0.029                    12473   
58                         0.154                    19911   
66                        -0.021                    15486   
114                        0.002                    10384   

     Private dwellings occupied by usual residents  \
3                                            15934   
4                                            12124   
58                                           19328   
66                                           15037   
114                                          10063   

     Population density per square kilometre  Land area in square kilometres  \
3                                      10863                            2.81   
4                                       2775                            9.98   
58                                      2712                           16.21   
66                                      6144                            7.16   
114                                     5073                            5.41   

     Children (0-14 years)  Youth (15-24 years)  Working Age (25-54 years)  \
3                     2360                 3750                      15040   
4                     3605                 2730                      10810   
58                    5820                 4695                      20640   
66                    6120                 5730                      17210   
114                   3885                 3225                      10675   

     Pre-retirement (55-64 years)  Seniors (65+ years)  \
3                            3480                 5910   
4                            3555                 6975   
58                           5400                 7405   
66                           5930                 8990   
114                          3510                 6160   

     Older Seniors (85+ years)  
3                         1040  
4                         1640  
58                        1480  
66                        1345  
114                       1220

In [65]:

folium.Choropleth(
    geo_data=map,
    name='choropleth',
    data=data,
    columns=['Neighbourhood Number', 'Seniors (65+ years)'],
    key_on='feature.properties.AREA_SHORT_CODE',
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2, 
).add_to(toronto_map65)

folium.LayerControl().add_to(toronto_map65)

In [123]:
toronto_map65

In [67]:
data65.sort_values(by='Older Seniors (85+ years)', ascending=False, na_position='first')

Neighbourhood Number  Population, 2016  Population, 2011  \
4                      42             27695             26918   
58                     14             43965             38084   
66                    117             43993             44919   
114                   118             27446             27398   
132                   137             53485             53350   
3                      95             30526             29177   

     Population Change 2011-2016  Total private dwellings  \
4                          0.029                    12473   
58                         0.154                    19911   
66                        -0.021                    15486   
114                        0.002                    10384   
132                        0.003                    19098   
3                          0.046                    18109   

     Private dwellings occupied by usual residents  \
4                                            12124   
58                                           19328   
66                                           15037   
114                                          10063   
132                                          18436   
3                                            15934   

     Population density per square kilometre  Land area in square kilometres  \
4                                       2775                            9.98   
58                                      2712                           16.21   
66                                      6144                            7.16   
114                                     5073                            5.41   
132                                     4345                           12.31   
3                                      10863                            2.81   

     Children (0-14 years)  Youth (15-24 years)  Working Age (25-54 years)  \
4                     3605                 2730                      10810   
58                    5820                 4695                      20640   
66                    6120                 5730                      17210   
114                   3885                 3225                      10675   
132                   9625                 7660                      21945   
3                     2360                 3750                      15040   

     Pre-retirement (55-64 years)  Seniors (65+ years)  \
4                            3555                 6975   
58                           5400                 7405   
66                           5930                 8990   
114                          3510                 6160   
132                          6245                 8010   
3                            3480                 5910   

     Older Seniors (85+ years)  
4                         1640  
58                        1480  
66                        1345  
114                       1220  
132                       1130  
3                         1040

In [68]:
data65.rename(columns={'Neighbourhood Number': 'AREA_SHORT_CODE'}, inplace=True)

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:4025: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  return super(DataFrame, self).rename(**kwargs)


In [90]:
data65

AREA_SHORT_CODE  Population, 2016  Population, 2011  \
3                 95             30526             29177   
4                 42             27695             26918   
58                14             43965             38084   
66               117             43993             44919   
114              118             27446             27398   
132              137             53485             53350   

     Population Change 2011-2016  Total private dwellings  \
3                          0.046                    18109   
4                          0.029                    12473   
58                         0.154                    19911   
66                        -0.021                    15486   
114                        0.002                    10384   
132                        0.003                    19098   

     Private dwellings occupied by usual residents  \
3                                            15934   
4                                            12124   
58                                           19328   
66                                           15037   
114                                          10063   
132                                          18436   

     Population density per square kilometre  Land area in square kilometres  \
3                                      10863                            2.81   
4                                       2775                            9.98   
58                                      2712                           16.21   
66                                      6144                            7.16   
114                                     5073                            5.41   
132                                     4345                           12.31   

     Children (0-14 years)  Youth (15-24 years)  Working Age (25-54 years)  \
3                     2360                 3750                      15040   
4                     3605                 2730                      10810   
58                    5820                 4695                      20640   
66                    6120                 5730                      17210   
114                   3885                 3225                      10675   
132                   9625                 7660                      21945   

     Pre-retirement (55-64 years)  Seniors (65+ years)  \
3                            3480                 5910   
4                            3555                 6975   
58                           5400                 7405   
66                           5930                 8990   
114                          3510                 6160   
132                          6245                 8010   

     Older Seniors (85+ years)  
3                         1040  
4                         1640  
58                        1480  
66                        1345  
114                       1220  
132                       1130

In [91]:
neighbourhood = map[['AREA_SHORT_CODE','AREA_NAME','LATITUDE','LONGITUDE']]

In [92]:
merged =pd.merge(data65, neighbourhood, on=['AREA_SHORT_CODE'])

In [93]:
merged.head(15)

AREA_SHORT_CODE  Population, 2016  Population, 2011  \
0               95             30526             29177   
1               42             27695             26918   
2               14             43965             38084   
3              117             43993             44919   
4              118             27446             27398   
5              137             53485             53350   

   Population Change 2011-2016  Total private dwellings  \
0                        0.046                    18109   
1                        0.029                    12473   
2                        0.154                    19911   
3                       -0.021                    15486   
4                        0.002                    10384   
5                        0.003                    19098   

   Private dwellings occupied by usual residents  \
0                                          15934   
1                                          12124   
2                                          19328   
3                                          15037   
4                                          10063   
5                                          18436   

   Population density per square kilometre  Land area in square kilometres  \
0                                    10863                            2.81   
1                                     2775                            9.98   
2                                     2712                           16.21   
3                                     6144                            7.16   
4                                     5073                            5.41   
5                                     4345                           12.31   

   Children (0-14 years)  Youth (15-24 years)  Working Age (25-54 years)  \
0                   2360                 3750                      15040   
1                   3605                 2730                      10810   
2                   5820                 4695                      20640   
3                   6120                 5730                      17210   
4                   3885                 3225                      10675   
5                   9625                 7660                      21945   

   Pre-retirement (55-64 years)  Seniors (65+ years)  \
0                          3480                 5910   
1                          3555                 6975   
2                          5400                 7405   
3                          5930                 8990   
4                          3510                 6160   
5                          6245                 8010   

   Older Seniors (85+ years)                        AREA_NAME   LATITUDE  \
0                       1040                       Annex (95)  43.671585   
1                       1640           Banbury-Don Mills (42)  43.737657   
2                       1480  Islington-City Centre West (14)  43.633463   
3                       1345                 L'Amoreaux (117)  43.795716   
4                       1220     Tam O'Shanter-Sullivan (118)  43.780130   
5                       1130                     Woburn (137)  43.766740   

   LONGITUDE  
0 -79.404001  
1 -79.349718  
2 -79.543317  
3 -79.314084  
4 -79.302919  
5 -79.228586

In [94]:
merged = merged.drop(columns = ['Population, 2016','Working Age (25-54 years)'])

In [95]:
merged = merged.drop(columns = ['Population, 2011','Population Change 2011-2016','Total private dwellings','Private dwellings occupied by usual residents'])

In [96]:
merged

AREA_SHORT_CODE  Population density per square kilometre  \
0               95                                    10863   
1               42                                     2775   
2               14                                     2712   
3              117                                     6144   
4              118                                     5073   
5              137                                     4345   

   Land area in square kilometres  Children (0-14 years)  Youth (15-24 years)  \
0                            2.81                   2360                 3750   
1                            9.98                   3605                 2730   
2                           16.21                   5820                 4695   
3                            7.16                   6120                 5730   
4                            5.41                   3885                 3225   
5                           12.31                   9625                 7660   

   Pre-retirement (55-64 years)  Seniors (65+ years)  \
0                          3480                 5910   
1                          3555                 6975   
2                          5400                 7405   
3                          5930                 8990   
4                          3510                 6160   
5                          6245                 8010   

   Older Seniors (85+ years)                        AREA_NAME   LATITUDE  \
0                       1040                       Annex (95)  43.671585   
1                       1640           Banbury-Don Mills (42)  43.737657   
2                       1480  Islington-City Centre West (14)  43.633463   
3                       1345                 L'Amoreaux (117)  43.795716   
4                       1220     Tam O'Shanter-Sullivan (118)  43.780130   
5                       1130                     Woburn (137)  43.766740   

   LONGITUDE  
0 -79.404001  
1 -79.349718  
2 -79.543317  
3 -79.314084  
4 -79.302919  
5 -79.228586

In [111]:


CLIENT_ID = '1RCTTAV1FRXKXARRUNTYW03BDHYBHMCLERFH11PPXCDU2ZYS'

CLIENT_SECRET = ''

VERSION = '20180323'

LIMIT = 30

In [112]:
def Venues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat,lng, 
        radius,
        LIMIT 
        )
         
       
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    # Convert the list to a datafrtame and define column name
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Borough', 
                  'Borough Latitude', 
                  'Borough Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [113]:
torontovenues = Venues(names=merged['AREA_NAME'],
                                 latitudes=merged['LATITUDE'],
                                 longitudes=merged['LONGITUDE'])

In [114]:
torontovenues.head()

Borough  Borough Latitude  Borough Longitude                   Venue  \
0  Annex (95)         43.671585         -79.404001            Ezra's Pound   
1  Annex (95)         43.671585         -79.404001             Rose & Sons   
2  Annex (95)         43.671585         -79.404001   Roti Cuisine of India   
3  Annex (95)         43.671585         -79.404001  The Madison Avenue Pub   
4  Annex (95)         43.671585         -79.404001                Big Crow   

   Venue Latitude  Venue Longitude       Venue Category  
0       43.675153       -79.405858                 Café  
1       43.675668       -79.403617  American Restaurant  
2       43.674618       -79.408249    Indian Restaurant  
3       43.667947       -79.403486                  Pub  
4       43.675896       -79.403680            BBQ Joint

In [115]:
torontovenues.count()

Borough              105
Borough Latitude     105
Borough Longitude    105
Venue                105
Venue Latitude       105
Venue Longitude      105
Venue Category       105
dtype: int64

In [116]:
torontovenues.groupby('Borough').count()

Borough Latitude  Borough Longitude  Venue  \
Borough                                                                       
Annex (95)                                     30                 30     30   
Banbury-Don Mills (42)                         22                 22     22   
Islington-City Centre West (14)                15                 15     15   
L'Amoreaux (117)                               19                 19     19   
Tam O'Shanter-Sullivan (118)                   15                 15     15   
Woburn (137)                                    4                  4      4   

                                 Venue Latitude  Venue Longitude  \
Borough                                                            
Annex (95)                                   30               30   
Banbury-Don Mills (42)                       22               22   
Islington-City Centre West (14)              15               15   
L'Amoreaux (117)                             19               19   
Tam O'Shanter-Sullivan (118)                 15               15   
Woburn (137)                                  4                4   

                                 Venue Category  
Borough                                          
Annex (95)                                   30  
Banbury-Don Mills (42)                       22  
Islington-City Centre West (14)              15  
L'Amoreaux (117)                             19  
Tam O'Shanter-Sullivan (118)                 15  
Woburn (137)                                  4

In [117]:
torontoven = folium.Map(
                location = [latitude, longitude], 
                zoom_start = 10)

In [118]:
folium.Choropleth(
    geo_data=map,
    name='choropleth',
    data=data,
    columns=['Neighbourhood Number', 'Seniors (65+ years)'],
    key_on='feature.properties.AREA_SHORT_CODE',
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2,
).add_to(torontoven)

folium.LayerControl().add_to(torontoven)

In [119]:
for index, row in torontovenues.iterrows():
    folium.Marker(location=[row['Venue Latitude'],row['Venue Longitude']],popup=row['Venue Category'],
).add_to(torontoven)

In [120]:
for index, row in torontovenues.iterrows():
    folium.Marker([row['Borough Latitude'], row['Borough Longitude']],
              popup=row['Borough'],
              icon=folium.Icon(color='red',icon='info-sign')
              ).add_to(torontoven)
 

In [121]:
folium.CircleMarker([43.795716,-79.314084],
                    radius=30,
                    popup="L'Amoreaux (117)",
                    color='red',
                    ).add_to(torontoven)

In [122]:
torontoven